In [1]:
import pandas as pd
import numpy as np
from codebase.file_utils import (
    save_obj,
    load_obj
)
import altair as alt
from codebase.data import flatten_matrix
alt.data_transformers.disable_max_rows()



DataTransformerRegistry.enable('default')

In [2]:
def plot_density(df, width=300, height=50) :
    return alt.Chart(df).transform_fold(
        ['value']
    ).transform_density(
        density='value',
        groupby=['var','source'],
    ).mark_area(opacity=0.5).encode(
        alt.X('value:Q'),
        alt.Y('density:Q'),
        alt.Row('var'),
        alt.Color('source')
    ).resolve_scale(
        x='independent'
    ).properties(width=width, height=height)


## 2 factor Sim EZ

In [25]:
def ibis_data(xdir):
    particles = load_obj('particles', xdir)
    particles.resample_particles()
    particles.reset_weights()
    return particles


def get_ibis_alpha(particles):
    samples = np.squeeze(particles.particles['alpha'])
    psdf = pd.DataFrame(
        samples, columns=['var'+str(i) for i in range(1,7)]
    ).reset_index().melt(id_vars = ['index'], var_name = ['var'])
    psdf['source'] = 'ibis'
    return psdf


def get_hmc_alpha(xdir2):
    ps = load_obj('ps', xdir2)
    samples = np.squeeze(ps['alpha'])[:,0,:]
    psdf_hmc = pd.DataFrame(
        samples, columns=['var'+str(i) for i in range(1,7)]
    ).reset_index().melt(id_vars = ['index'], var_name = ['var'])
    psdf_hmc['source'] = 'hmc'
    return psdf_hmc


def get_ibis_beta(particles, J, K):
    betabeta = np.empty((1000, J*K))
    for i in range(1000):
        b = particles.particles['beta'][i,0]
        betabeta[i] = b.flatten()
    psdf = pd.DataFrame(
    betabeta, columns=['var'+str(i) for i in range(J*K)]
    ).reset_index().melt(id_vars = ['index'], var_name = ['var'])
    psdf['source'] = 'ibis'
    return psdf



def get_ibis_betabeta(particles, J):
    betabeta = np.empty((1000, int((J**2-J)/2+J)))
    for i in range(1000):
        b = particles.particles['beta'][i,0]
        betabeta[i] = flatten_matrix(b @ b.T)
    psdf = pd.DataFrame(
    betabeta, columns=['var'+str(i) for i in range(int((J**2-J)/2+J))]
    ).reset_index().melt(id_vars = ['index'], var_name = ['var'])
    psdf['source'] = 'ibis'
    return psdf


def get_hmc_beta(xdir2, J, K):
    ps = load_obj('ps', xdir2)
    samples = np.squeeze(ps['beta'])[:,0]
    betabeta = np.empty((1000, J*K))
    for i in range(1000):
        b = samples[i]
        betabeta[i] = b.flatten()

    psdf_hmc = pd.DataFrame(
        betabeta, columns=['var'+str(i) for i in range(J*K)]
    ).reset_index().melt(id_vars = ['index'], var_name = ['var'])
    psdf_hmc['source'] = 'hmc'
    return psdf_hmc


def get_hmc_betabeta(xdir2, J):
    ps = load_obj('ps', xdir2)
    samples = np.squeeze(ps['beta'])[:,0]
    betabeta = np.empty((1000, int((J**2-J)/2+J)))
    for i in range(1000):
        b = samples[i]
        betabeta[i] = flatten_matrix(b @ b.T)

    psdf_hmc = pd.DataFrame(
        betabeta, columns=['var'+str(i) for i in range(int((J**2-J)/2+J))]
    ).reset_index().melt(id_vars = ['index'], var_name = ['var'])
    psdf_hmc['source'] = 'hmc'
    return psdf_hmc

## EZ comparisons

In [26]:
xdir2 = '../../bayes-sem/src/log/cont_sim_data/PPP/20201128_144959_reruncont_s0m1/'
particles = ibis_data('./log/20201207_230922_sim_ez/')

In [27]:
## alpha
plot_density(pd.concat([
    get_ibis_alpha(particles), get_hmc_alpha(xdir2)
])
)

alt.Chart(...)

In [28]:
## beta
plot_density(
    pd.concat([
        get_ibis_beta(particles, 6, 2),
        get_hmc_beta(xdir2, 6, 2)
        ]),
    height=100
)

alt.Chart(...)

In [29]:
## betabeta
plot_density(
    pd.concat([
        get_ibis_betabeta(particles, 6),
        get_hmc_betabeta(xdir2, 6)
        ]),
    height=100
)

alt.Chart(...)

## AZ comparisons

In [33]:
xdir2 = '../../bayes-sem/src/log/cont_sim_data/PPP/20201128_145015_reruncont_s0m2//'
particles = ibis_data('./log/20201207_230712_sim_az/')

In [34]:
## alpha
plot_density(pd.concat([
    get_ibis_alpha(particles), get_hmc_alpha(xdir2)
])
)

alt.Chart(...)

In [36]:
## beta
plot_density(
    pd.concat([
        get_ibis_beta(particles, 6,2),
        get_hmc_beta(xdir2, 6,2)
        ]),
    height=100
).interactive()

alt.Chart(...)